# Convert Phase 2 well data
Locher Environmental recorded data from multiple transducers in two adjacent wells near SLC 39A at Kennedy Space Center (KSC), between March and November, 2022. This was part of a seismo-acoustic erosion pilot experiment. During phase 2 of the experiment, which began on July 21st, 2022, vibrating wire sensors were used and found to give more accurate water levels. These data were captured on Campbell Scientific dataloggers and recorded in TOB3 binary file format. The purpose of this notebook is to:
- read these files
- apply calibration equations
- write to pickle files (Python binary files that serialize the data variables)
Calibration constants are defined in the transducers dataframe (section 2). These are copied from the file "A Pz Linear Gage Calc_NASA Sensors.xls". Other metadata included in this dataframe come from sections 6 and 7 in the file "2022-12-03_ Field Sheet for Deployment of Groundwater Equipment at NASA_Part_II.pdf".

Note on *TIME ZONES*: 
- Local time is used in Campbell Scientific binary files, and files converted to Pickle.
- UTC is used in MiniSEED files, to match seismo-acoustic data.

Note on *UNITS*:
- Pi

To do:
- create a lookup table, matching file name, start time, end time, and SEED trace-ID.


# 1. Imports, path variables, and function definitions

In [5]:
# raw data on April 1, 2022 from 16:10 to 16:40 UTC. Launch from SLC40 at 16:24 UTC, watched from Titusville
import os, sys, glob, obspy
import numpy as np
import pandas as pd

import platform
osname = platform.system()
print(osname)

cwd = os.getcwd()
sys.path.append(os.path.join(cwd, 'campbell'))
import read_cs_files as campbell
HOME = os.getenv('HOME')
sys.path.append(os.path.join(HOME, 'src', 'kitchensinkGT', 'LIB'))
from libseisGT import write_stream2sds, read_sds, open_sds, sds_get_nonempty_traceids, sds_percent_available_per_day

if osname=='Darwin':
    DROPBOX_TOP = os.path.join(HOME, 'Dropbox')
    SDS_TOP = os.path.join(DROPBOX_TOP, 'DATA', 'SDS')
    WELLDATA_TOP = os.path.join(DROPBOX_TOP, 'DATA', 'KSC', 'KSC_Well_Seismoacoustic_Data/WellData')
    TOB3_DIR = os.path.join(WELLDATA_TOP, 'Uploads')
    PKL_DIR = os.path.join(WELLDATA_TOP, 'Converted')
elif osname=='Linux':
    DROPBOX_TOP = '/raid/newhome/thompsong/Dropbox'
    SDS_TOP = os.path.join(HOME, 'SDS')
    if not os.path.isdir(SDS_TOP):
        os.mkdir(SDS_TOP)
    WELLDATA_TOP = os.path.join(DROPBOX_TOP, 'DATA', 'KSC', 'KSC_Well_Seismoacoustic_Data/WellData')
    TOB3_DIR = os.path.join(WELLDATA_TOP, 'Uploads')
    PKL_DIR = os.path.join(HOME, 'Converted')    
#DROPBOX_PROJECT_DIR = os.path.join(DROPBOX_TOP, 'PROFESSIONAL/RESEARCH/3_Project_Documents/NASAprojects/201602 Rocket Seismology/202010 KSC Launchpad Erosion')
#EVENT_MSEED_DIR = os.path.join(DROPBOX_TOP, 'DATA', 'KSC', 'KSC_Well_Seismoacoustic_Data/SeismoAcousticData/Events')

if not os.path.isdir(PKL_DIR):
    os.mkdir(PKL_DIR)

def measureClockDrift(df):
    passed = True
    starttime=df.iloc[0]['TIMESTAMP']
    endtime=df.iloc[-1]['TIMESTAMP']
    timediff = (endtime - starttime)
    nrows=len(df.index)
    numValidTimes = nrows
    secs = np.array([x.timestamp() for x in df['TIMESTAMP']])
    recs = df['RECORD'].to_numpy().astype('int')
    recsdiff = recs[1:-1]-recs[0:-2]
    #print(recsdiff)
    secsdiff = secs[1:-1]-secs[0:-2]   
    print(secsdiff)
    sample_interval = np.nanmedian(secsdiff)
    gps_records = []
    for i in range(0,len(secsdiff)):
        thisdiff = secsdiff[i]
        if thisdiff >= sample_interval*(recsdiff[i]+0.5) or thisdiff <= sample_interval*(recsdiff[i]-0.5):
            # recsdiff suggests consecutive samples, but thisdiff suggests a strange jump in sample time
            # we assume the GPS clock jumped in and reset. these are the times we save for interpolation
            gps_records.append(df.iloc[i]['RECORD'])
            gps_records.append(df.iloc[i+1]['RECORD'])
            try: # this might not always exist if at end of file
                gps_records.append(df.iloc[i+2]['RECORD']) 
            except:
                pass
    df2 = df[df['RECORD'].isin(gps_records)]    
    print('GPS timed samples')
    print(df2)
    return df2
    #input('Press ENTER to continue')


def compute_psi(dig, d):
    psi = np.zeros((len(dig),1))
    #if np.isnan(d['dig0']):
    #    return psi
    for i in range(len(dig)):
        psi[i] = ((dig[i]-d['dig0']) * d['gf'] + (d['tt']-d['tt0'])*d['tf']+(d['bp0']-d['bp']))
        
    #print(level)
    return psi

def psi2pascals(psi):
    psi2kPa = 6.894757
    Pa = psi * psi2kPa * 1000
    return Pa

def psi2depthmetres(psi):
    psi2kPa = 6.894757
    kPa2mH20 = 0.101974
    mH20 = psi * psi2kPa * kPa2mH20
    return mH20

def localtime2utc(this_dt):
    hours = 4
    if this_dt>obspy.UTCDateTime(2022,11,6,2,0,0):
        hours = 5
    localTimeCorrection = 3600 * hours
    return this_dt + localTimeCorrection
    
def convert2sds(df, SDS_TOP):
    local_startt = obspy.UTCDateTime(df.iloc[0]['TIMESTAMP'])
    nextt = obspy.UTCDateTime(df.iloc[1]['TIMESTAMP'])
    dt = nextt-local_startt
    utc_startt = localtime2utc(local_startt)
    if utc_startt > obspy.UTCDateTime():
        return
        
    st = obspy.Stream()    
        
    for col in df.columns[2:]:
        print('Processing column %s' % col)
        this_transducer = transducersDF[(transducersDF['serial']) == col]
        if len(this_transducer.index)==1:
            this_transducer = this_transducer.iloc[0].to_dict()
            tr = obspy.Trace()
            tr.id = this_transducer['id']
            if tr.stats.sampling_rate==20:
                if tr.stats.channel[0]=='H':
                    tr.stats.channel="B%s" % tr.stats.channel[1:]
            tr.stats.starttime = utc_startt
            tr.stats.delta = dt  
            tr.data = np.array(df[col])
            #print(tr)
            st.append(tr)
    print('Final Stream object to write')
    sdsclient = open_sds(SDS_TOP)
    try:
        write_stream2sds(st, sdsclient)
    except:
        for tr in st:
            new_st= Stream()
            new_st.append(tr)
            try:
                write_stream2sds(new_st, sdsclient)
            except:
                pass
    del sdsclient
    
def convert2units(st):
    for tr in st:
        if tr.stats.network=='FL':
            continue
        try:
            this_transducer = transducersDF[(transducersDF['id']) == tr.id] # not working
        except:
            for i,rows in transducersDF.iterrows():
                if row['id'] == tr.id:
                    this_transducer = row
        if this_transducer['type']=='level':
            tr.data = psi2depthmetres(tr.data)
        elif this_transducer['type']=='pressure':
            tr.data = psi2pascals(tr.data)
       

Linux


# 2. Define phase 2 lookup table & conversions

(From "2022-12-03_ Field Sheet for Deployment of Groundwater Equipment at NASA_Part_II.pdf")

In [3]:
phase2_startdate = obspy.UTCDateTime(2022,7,21,14,7,0)
transducers = []

# Shallow well (HOF-IW0006S)
transducer1 = {'serial':'AirPressureShallow', 'Fs':100, 'sensor':'barometer','shielding':'none',
               'range_kPa_low':100,'range_kPa_high':100,'media':'air', 'type':'pressure', 
               'model':'Keller 0507.01401.051311.07','set_depth_ft':4.46, 'id':'6S.02374.88.HDH'
              } # serial 237488
transducers.append(transducer1)
transducer2 = {'serial':'1226420', 'Fs':100, 'sensor':'vibrating_wire','shielding':'none',
               'range_kPa_low':70,'range_kPa_high':170,'media':'water', 'type':'level', 
               'model':'Geokon 4500AL','set_depth_ft':3.81,
               'dig0':9751, 'gf':-0.006458, 'tt':21.6, 'tt0':21.3, 'tf':-0.008795, 
               'bp':0.0, 'bp0':14.298, 'id':'6S.12264.20.HDD'
              }
transducers.append(transducer2)
transducer3 = {'serial':'1226423', 'Fs':20, 'sensor':'vibrating_wire','shielding':'foam',
               'range_kPa_low':70,'range_kPa_high':170,'media':'water', 'type':'level', 
               'model':'Geokon 4500AL','set_depth_ft':-5.83,
               'dig0':9605, 'gf':-0.006347, 'tt':21.6, 'tt0':22.2, 'tf':-0.004197, 
               'bp':14.504, 'bp0':14.298, 'id':'6S.12264.23.BDD'
              }
transducers.append(transducer3)
transducer4 = {'serial':'1226419', 'Fs':100, 'sensor':'vibrating_wire','shielding':'foam',
               'range_kPa_low':70,'range_kPa_high':170,'media':'water', 'type':'level', 
               'model':'Geokon 4500AL','set_depth_ft':-6.71,
               'dig0':10040, 'gf':-0.006441, 'tt':21.6, 'tt0':21.1, 'tf':-0.010870, 
               'bp':14.504, 'bp0':14.298, 'id':'6S.12264.19.HDD'
              }
transducers.append(transducer4)
transducer5 = {'serial':'1226421', 'Fs':100, 'sensor':'vibrating_wire','shielding':'none',
               'range_kPa_low':70,'range_kPa_high':170,'media':'water', 'type':'level', 
               'model':'Geokon 4500AL','set_depth_ft':-7.71,
               'dig0':9787, 'gf':-0.006724, 'tt':21.6, 'tt0':21.3, 'tf':-0.001145, 
               'bp':14.504, 'bp0':14.298, 'id':'6S.12264.21.HDD'           
               }
transducers.append(transducer5)

# Intermediate well (HOF-IW00061)
transducer6 = {'serial':'AirPressureDeep', 'Fs':100, 'sensor':'barometer','shielding':'none',
               'range_kPa_low':100,'range_kPa_high':100,'media':'air', 'type':'pressure', 
               'model':'Keller 0507.01401.051311.07','set_depth_ft':4.46, 'id':'6I.0XXXX.XX.HDH'
              }
transducers.append(transducer6)
transducer7 = {'serial':'1226429', 'Fs':100, 'sensor':'vibrating_wire','shielding':'none',
               'range_kPa_low':70,'range_kPa_high':170,'media':'water', 'type':'level', 
               'model':'Geokon 4500AL','set_depth_ft':3.71,
               'dig0':9800, 'gf':-0.006428, 'tt':22.6, 'tt0':21.6, 'tf':-0.002384, 
               'bp':0.0, 'bp0':14.298, 'id':'6I.12264.29.HDD'          
              }
transducers.append(transducer7)
transducer8 = {'serial':'2151692', 'Fs':20, 'sensor':'vibrating_wire','shielding':'foam',
               'range_kPa_low':70,'range_kPa_high':170,'media':'water', 'type':'level', 
               'model':'Geokon 4500AL','set_depth_ft':-9.29,
               'dig0':9459, 'gf':-0.008038, 'tt':22.8, 'tt0':21.8, 'tf':-0.007666, 
               'bp':14.296, 'bp0':14.388, 'id':'6I.21516.92.BDD'
              }
transducers.append(transducer8)
transducer9 = {'serial':'2151691', 'Fs':100, 'sensor':'vibrating_wire','shielding':'foam',
               'range_kPa_low':70,'range_kPa_high':170,'media':'water', 'type':'level', 
               'model':'Geokon 4500AL','set_depth_ft':-18.46,
               'dig0':9414, 'gf':-0.008142, 'tt':22.8, 'tt0':21.5, 'tf':-0.008742, 
               'bp':14.296, 'bp0':14.388, 'id':'6I.21516.91.HDD'
              }
transducers.append(transducer9)
transducer10 = {'serial':'2149882', 'Fs':100, 'sensor':'vibrating_wire','shielding':'none',
               'range_kPa_low':70,'range_kPa_high':170,'media':'water', 'type':'level', 
               'model':'Geokon 4500AL','set_depth_ft':-19.29,
               'dig0':9734, 'gf':-0.008075, 'tt':20.7, 'tt0':21.3, 'tf':-0.000675, 
               'bp':14.602, 'bp0':14.389, 'id':'6I.21498.82.HDD'
               }
transducers.append(transducer10)
transducersDF = pd.DataFrame(transducers)
print(transducersDF)
outfile = os.path.join(WELLDATA_TOP, 'transducer_metadata.csv')
transducersDF.to_csv(outfile)

               serial   Fs          sensor shielding  range_kPa_low  \
0  AirPressureShallow  100       barometer      none            100   
1             1226420  100  vibrating_wire      none             70   
2             1226423   20  vibrating_wire      foam             70   
3             1226419  100  vibrating_wire      foam             70   
4             1226421  100  vibrating_wire      none             70   
5     AirPressureDeep  100       barometer      none            100   
6             1226429  100  vibrating_wire      none             70   
7             2151692   20  vibrating_wire      foam             70   
8             2151691  100  vibrating_wire      foam             70   
9             2149882  100  vibrating_wire      none             70   

   range_kPa_high  media      type                        model  set_depth_ft  \
0             100    air  pressure  Keller 0507.01401.051311.07          4.46   
1             170  water     level                Geokon

# 3. Read raw data files, apply calibration equations, write out to pickle and SDS

In [6]:
# Read Campbell Scientific TOB3 file
write_csv = False
write_raw = False
print_dfs = False
keep_existing = False
allcolumns = []
#MAXFILES = 124
MAXFILES=9999
lod = []

tob3files = []
uploaddirs = sorted(glob.glob(os.path.join(TOB3_DIR, '20??????')))
for uploaddir in uploaddirs:
    tob3files_100Hz = sorted(glob.glob(os.path.join(uploaddir, '100hz/*.dat')))
    tob3files.extend(tob3files_100Hz)
    tob3files_baro = sorted(glob.glob(os.path.join(uploaddir,  'Baro/*.dat')))
    tob3files.extend(tob3files_baro)
    tob3files_20Hz = sorted(glob.glob(os.path.join(uploaddir,  '20hz/*.dat')))
    tob3files.extend(tob3files_20Hz)

maxfiles = min([len(tob3files), MAXFILES])
for filenum, tob3file in enumerate(tob3files[0:MAXFILES]):
    tob3base = os.path.basename(tob3file)
    print('File %d of %d: %s' % ((filenum+1), maxfiles, tob3file))
    dirname = os.path.basename(os.path.dirname(tob3file))
    pklfile = os.path.join(PKL_DIR, "%s.%s.%s.pkl" % (os.path.basename(uploaddir), dirname, tob3base)).replace('.dat','')
    if os.path.isfile(pklfile) & keep_existing:
        print('- Already DONE')
        df2 = pd.read_pickle(pklfile)
    else:
        print('- Reading')
        data, meta = campbell.read_cs_files(tob3file, forcedatetime=False,
                      bycol=True, quiet=True, metaonly=False)
        print('- converting to dataframe')
        try: # adding because one time meta was just a bool and not subscriptable
            df = pd.DataFrame(columns=meta[2]) 
        except:
            continue
        for c in range(len(meta[2])):
            df[meta[2][c]] = data[c]
            if not meta[2][c] in allcolumns:
                allcolumns.append(meta[2][c])       
            
        #if print_dfs:
        #    print(df)
        if write_csv & write_raw:
            csvfile = pklfile.replace('.pkl','_raw.csv')
            print('- writing raw data to %s' % csvfile)
            df.to_csv(csvfile)
        if write_raw:
            pklfile = pklfile.replace('.pkl','_raw.pkl')
            print('- writing raw data to %s' % pklfile)
            df.to_pickle(pklfile)
    
        print('- Applying calibration equations')
        df2 = df.copy()
        for col in df2.columns:
            #print(col)
            if col[0:2]=='12' or col[0:2]=='21':
                this_transducer = transducersDF[(transducersDF['serial']) == col]
                #print(this_transducer)
                if len(this_transducer.index)==1:
                    this_transducer = this_transducer.iloc[0].to_dict()
                    #print(this_transducer)
                    df2[col] = compute_psi(df2[col].to_numpy(), this_transducer)
    if print_dfs:
        print('Converted dataframe:')
        print(df2)
        
    # check start & end time 
    passed = True
    starttime=df2.iloc[0]['TIMESTAMP']
    endtime=df2.iloc[-1]['TIMESTAMP']
    timediff = (endtime - starttime)
    nrows=len(df2.index)
    numValidTimes = nrows
    secs = np.array([x.timestamp() for x in df2['TIMESTAMP']])
    secsdiff = secs[1:-1]-secs[0:-2]
    sample_interval = np.nanmedian(secsdiff)
    #sample_interval2 = timediff.seconds/(nrows-1)  
    if timediff.seconds>4*60*60: # files should be no more than 4 hours
        print('Problem likely with start time. Filter out all data more than 4 hours before end')
        df2 = df2[df2['TIMESTAMP']>endtime-pd.to_timedelta(4, unit='h')]
        df2 = df2[df2['TIMESTAMP']<=endtime]
        numValidTimes = len(df2.index)
        passed = False

    # check clock drift
    gpsdf = measureClockDrift(df2)
    if not gpsdf.empty:
        # write oout
        gpspkl = pklfile.replace('.pkl','_gps.pkl')
        gpsdf.to_pickle(gpspkl)
        passed = False
    
    if write_csv:
        csvfile = pklfile.replace('.pkl','.csv')
        print('- writing calibrated data to %s' % csvfile)
        df2.to_csv(csvfile)    
        
    print('- writing calibrated data to %s' % pklfile)       
    df2.to_pickle(pklfile)
    
    #print('- writing to SDS')
    #convert2sds(df2, SDS_TOP)
    
    print('- DONE\n')
    thisd = {}
    thisd['filename']=os.path.basename(pklfile)
    thisd['starttime']=starttime
    thisd['endtime']=endtime
    thisd['hours']=np.round(timediff.seconds/3600.0,2)
    thisd['npts']=nrows
    thisd['nRECS']=df2.iloc[-1]['RECORD']-df2.iloc[0]['RECORD']+1
    thisd['Fs']=1/sample_interval
    if thisd['nRECS']!=nrows:
        passed=False
    if numValidTimes<nrows:
        passed=False
    thisd['numValidTimes']=numValidTimes
    thisd['numTimeSkips']=len(gpsdf.index)/3
    thisd['passed']=passed
    lod.append(thisd)
    lookuptableDF = pd.DataFrame(lod)
    print(lookuptableDF)
    lookuptableDF.to_csv('lookuptable.csv')    
input('ENTER')

File 1 of 2117: /raid/newhome/thompsong/Dropbox/DATA/KSC/KSC_Well_Seismoacoustic_Data/WellData/Uploads/20220826/100hz/100hz_Sensors_100Hz0.dat
- Reading
- converting to dataframe
- Applying calibration equations
[ 0.00999999  0.00999999  0.00999999 ...,  0.00999999  0.00999999
  0.00999999]
GPS timed samples
                  TIMESTAMP  RECORD   1226421   1226419    1226420   2149882  \
105 2022-07-21 13:36:28.050     105       NaN       NaN        NaN       NaN   
106 2022-07-21 13:36:29.000     106  3.983720  3.368830  14.625066  8.751349   
107 2022-07-21 13:36:29.010     107  3.982603  3.351595  14.625312  8.748818   

      2151691    1226429  
105       NaN        NaN  
106  8.692963  14.497200  
107  8.697090  14.499341  
- writing calibrated data to /home/thompsong/Converted/20221202.100hz.100hz_Sensors_100Hz0.pkl
- DONE

                                  filename           starttime  \
0  20221202.100hz.100hz_Sensors_100Hz0.pkl 2022-07-21 13:36:27   

              endtime  ho

- converting to dataframe
- Applying calibration equations
[ 0.00999999  0.00999999  0.00999999 ...,  0.00999999  0.00999999
  0.00999999]
GPS timed samples
                      TIMESTAMP    RECORD   1226421   1226419    1226420  \
36299   2022-07-23 16:06:03.000  18176466       NaN       NaN        NaN   
36300   2022-07-23 16:06:04.000  18176467  3.911614  3.317793  14.656890   
36301   2022-07-23 16:06:04.010  18176468  3.924248  3.327140  14.670405   
1216100 2022-07-23 19:22:42.000  19356267       NaN       NaN        NaN   
1216101 2022-07-23 19:22:43.000  19356268  3.910774  3.293010  14.664735   
1216102 2022-07-23 19:22:43.010  19356269  3.905632  3.282675  14.670531   

          2149882   2151691    1226429  
36299         NaN       NaN        NaN  
36300    8.673107  8.627390  14.533050  
36301    8.704184  8.619717  14.537206  
1216100       NaN       NaN        NaN  
1216101  8.666703  8.641193  14.416499  
1216102  8.664361  8.642402  14.557588  
- writing calibrated da

- converting to dataframe
- Applying calibration equations
[ 0.00999999  0.00999999  0.00999999 ...,  0.00999999  0.00999999
  0.00999999]
GPS timed samples
Empty DataFrame
Columns: [TIMESTAMP, RECORD, 1226421, 1226419, 1226420, 2149882, 2151691, 1226429]
Index: []
- writing calibrated data to /home/thompsong/Converted/20221202.100hz.100hz_Sensors_100Hz17.pkl
- DONE

                                   filename                  starttime  \
0   20221202.100hz.100hz_Sensors_100Hz0.pkl 2022-07-21 13:36:27.000000   
1   20221202.100hz.100hz_Sensors_100Hz1.pkl 2056-05-27 07:07:24.924000   
2  20221202.100hz.100hz_Sensors_100Hz10.pkl 2022-07-23 04:00:00.010000   
3  20221202.100hz.100hz_Sensors_100Hz11.pkl 2022-07-23 08:00:00.010000   
4  20221202.100hz.100hz_Sensors_100Hz12.pkl 2022-07-23 12:00:00.010000   
5  20221202.100hz.100hz_Sensors_100Hz13.pkl 2022-07-23 16:00:00.010000   
6  20221202.100hz.100hz_Sensors_100Hz14.pkl 2056-07-14 20:14:01.041800   
7  20221202.100hz.100hz_Sensors_100Hz1

- converting to dataframe
- Applying calibration equations
[ 0.00999999  0.00999999  0.00999999 ...,  0.00999999  0.00999999
  0.00999999]
GPS timed samples
                     TIMESTAMP   RECORD   1226421   1226419    1226420  \
119299 2022-07-21 20:19:53.000  2420506       NaN       NaN        NaN   
119300 2022-07-21 20:19:54.000  2420507  3.961532  3.366390  14.598869   
119301 2022-07-21 20:19:54.010  2420508  3.972255  3.340676  14.607906   
129200 2022-07-21 20:21:33.000  2430407       NaN       NaN        NaN   
129201 2022-07-21 20:21:34.000  2430408  3.975249  3.327869  14.614969   
129202 2022-07-21 20:21:34.010  2430409  3.977455  3.326253  14.600666   

         2149882   2151691    1226429  
119299       NaN       NaN        NaN  
119300  8.719073  8.678794  14.484853  
119301  8.715705  8.679645  14.467483  
129200       NaN       NaN        NaN  
129201  8.738030  8.692733  14.481997  
129202  8.712456  8.668291  14.485845  
- writing calibrated data to /home/thompsong

- converting to dataframe
- Applying calibration equations
[ 0.00999999  0.00999999  0.00999999 ...,  0.00999999  0.00999999
  0.00999999]
GPS timed samples
                      TIMESTAMP    RECORD   1226421   1226419    1226420  \
1062199 2022-07-25 06:57:02.000  32161772       NaN       NaN        NaN   
1062200 2022-07-25 06:57:03.000  32161773  3.847835  3.238343  14.661046   
1062201 2022-07-25 06:57:03.010  32161774  3.864415  3.261283  14.661979   

          2149882   2151691    1226429  
1062199       NaN       NaN        NaN  
1062200  8.648251  8.563908  14.642276  
1062201  8.630618  8.561777  14.493195  
- writing calibrated data to /home/thompsong/Converted/20221202.100hz.100hz_Sensors_100Hz22.pkl
- DONE

                                    filename                  starttime  \
0    20221202.100hz.100hz_Sensors_100Hz0.pkl 2022-07-21 13:36:27.000000   
1    20221202.100hz.100hz_Sensors_100Hz1.pkl 2056-05-27 07:07:24.924000   
2   20221202.100hz.100hz_Sensors_100Hz10.pkl 

...

- converting to dataframe
- Applying calibration equations
Problem likely with start time. Filter out all data more than 4 hours before end
[ 0.04999995  0.04999995  0.05000019 ...,  0.04999995  0.05000019
  0.04999995]
GPS timed samples
                   TIMESTAMP    RECORD   1226423   2151692
928  2022-11-24 09:40:44.000  21647375       NaN       NaN
929  2022-11-24 09:40:45.000  21647376  3.705818  8.651264
930  2022-11-24 09:40:45.050  21647377  3.485551  8.651602
2069 2022-11-24 09:41:42.000  21648516       NaN       NaN
2070 2022-11-24 09:41:43.000  21648517  3.413050  8.652143
2071 2022-11-24 09:41:43.050  21648518  3.490609  8.651955
- writing calibrated data to /home/thompsong/Converted/20221202.20hz.20hz_Sensors_20Hz89.pkl
- DONE

                                      filename               starttime  \
0      20221202.100hz.100hz_Sensors_100Hz0.pkl 2022-07-21 13:36:27.000   
1      20221202.100hz.100hz_Sensors_100Hz1.pkl 2056-05-27 07:07:24.924   
2     20221202.100hz.100hz

- converting to dataframe
- Applying calibration equations
[ 0.04999995  0.05000019  0.04999995 ...,  0.04999995  0.04999995
  0.04999995]
GPS timed samples
Empty DataFrame
Columns: [TIMESTAMP, RECORD, 1226423, 2151692]
Index: []
- writing calibrated data to /home/thompsong/Converted/20221202.20hz.20hz_Sensors_20Hz91.pkl
- DONE

                                      filename               starttime  \
0      20221202.100hz.100hz_Sensors_100Hz0.pkl 2022-07-21 13:36:27.000   
1      20221202.100hz.100hz_Sensors_100Hz1.pkl 2056-05-27 07:07:24.924   
2     20221202.100hz.100hz_Sensors_100Hz10.pkl 2022-07-23 04:00:00.010   
3     20221202.100hz.100hz_Sensors_100Hz11.pkl 2022-07-23 08:00:00.010   
4     20221202.100hz.100hz_Sensors_100Hz12.pkl 2022-07-23 12:00:00.010   
...                                        ...                     ...   
2099     20221202.20hz.20hz_Sensors_20Hz88.pkl 2022-11-23 16:00:00.050   
2100     20221202.20hz.20hz_Sensors_20Hz89.pkl 2022-11-23 19:40:17.100   
210

- converting to dataframe
- Applying calibration equations
[ 0.04999995  0.05000019  0.04999995 ...,  0.04999995  0.05000019
  0.04999995]
GPS timed samples
Empty DataFrame
Columns: [TIMESTAMP, RECORD, 1226423, 2151692]
Index: []
- writing calibrated data to /home/thompsong/Converted/20221202.20hz.20hz_Sensors_20Hz94.pkl
- DONE

                                      filename               starttime  \
0      20221202.100hz.100hz_Sensors_100Hz0.pkl 2022-07-21 13:36:27.000   
1      20221202.100hz.100hz_Sensors_100Hz1.pkl 2056-05-27 07:07:24.924   
2     20221202.100hz.100hz_Sensors_100Hz10.pkl 2022-07-23 04:00:00.010   
3     20221202.100hz.100hz_Sensors_100Hz11.pkl 2022-07-23 08:00:00.010   
4     20221202.100hz.100hz_Sensors_100Hz12.pkl 2022-07-23 12:00:00.010   
...                                        ...                     ...   
2102     20221202.20hz.20hz_Sensors_20Hz90.pkl 2022-11-24 12:00:00.050   
2103     20221202.20hz.20hz_Sensors_20Hz91.pkl 2022-11-24 16:00:00.050   
210

- converting to dataframe
- Applying calibration equations
[ 0.04999995  0.05000019  0.04999995 ...,  0.04999995  0.05000019
  0.04999995]
GPS timed samples
Empty DataFrame
Columns: [TIMESTAMP, RECORD, 1226423, 2151692]
Index: []
- writing calibrated data to /home/thompsong/Converted/20221202.20hz.20hz_Sensors_20Hz97.pkl
- DONE

                                      filename               starttime  \
0      20221202.100hz.100hz_Sensors_100Hz0.pkl 2022-07-21 13:36:27.000   
1      20221202.100hz.100hz_Sensors_100Hz1.pkl 2056-05-27 07:07:24.924   
2     20221202.100hz.100hz_Sensors_100Hz10.pkl 2022-07-23 04:00:00.010   
3     20221202.100hz.100hz_Sensors_100Hz11.pkl 2022-07-23 08:00:00.010   
4     20221202.100hz.100hz_Sensors_100Hz12.pkl 2022-07-23 12:00:00.010   
...                                        ...                     ...   
2105     20221202.20hz.20hz_Sensors_20Hz93.pkl 2022-11-25 12:00:00.050   
2106     20221202.20hz.20hz_Sensors_20Hz94.pkl 2022-11-25 16:00:00.050   
210

''

To do: load and concat the gps pkl files. look for patterns. and study the lookuptable.csv too

In [11]:
gpspklfiles = sorted(glob.glob(os.path.join(PKL_DIR,'*Baro*_gps.pkl')))
masterdf = pd.DataFrame()
for gpsfile in gpspklfiles:
    thisdf = pd.read_pickle(gpsfile)
    if len(masterdf.index)==0:
        masterdf = thisdf
    else:
        masterdf = pd.concat([masterdf, thisdf])
print(masterdf)

                      TIMESTAMP     RECORD  AirPressureShallow  \
17737   2022-11-04 10:13:53.590      17737           10.152663   
17738   2022-11-04 10:14:14.730      17738           14.796425   
17739   2022-11-04 10:14:14.740      17739           14.797110   
1122500 2022-08-07 07:07:05.000  144436223           14.812943   
1122501 2022-08-07 07:07:05.130  144436224           14.817218   
...                         ...        ...                 ...   
159409  2022-08-07 00:26:34.130  142033128           14.827829   
159410  2022-08-07 00:26:34.140  142033129           14.831511   
1315206 2022-08-07 03:39:12.100  143188925           14.806129   
1315207 2022-08-07 03:39:12.030  143188926           14.806801   
1315208 2022-08-07 03:39:12.040  143188927           14.806429   

         AirPressureDeep  
17737          10.152692  
17738          14.790243  
17739          14.788268  
1122500        14.808659  
1122501        14.812721  
...                  ...  
159409         14.

In [13]:
gpspklfiles = sorted(glob.glob(os.path.join(PKL_DIR,'*100hz_Sensors*_gps.pkl')))
masterdf = pd.DataFrame()
for gpsfile in gpspklfiles:
    thisdf = pd.read_pickle(gpsfile)
    if len(masterdf.index)==0:
        masterdf = thisdf
    else:
        masterdf = pd.concat([masterdf, thisdf])
print(masterdf)

            1226419       1226420    1226421    1226429    2149882    2151691  \
14500           NaN           NaN        NaN        NaN        NaN        NaN   
14501  3.382146e+00     14.572053   3.992007  14.463139   9.161526   8.713390   
14502  3.384178e+00     14.562517   3.984665  14.491212   8.790375   8.724625   
26701           NaN           NaN        NaN        NaN        NaN        NaN   
26702  3.394059e+00     14.560335   3.975420  14.510270   9.531383   8.710169   
...             ...           ...        ...        ...        ...        ...   
14399  3.313522e+00     14.654172   3.943875  14.519322   8.701172   8.656610   
14400 -3.312400e+19 -21084.307080  24.420155  77.290016  78.389455  76.729423   
14401 -1.204280e+20 -20978.499209  24.204830  77.290016  78.389455  76.729423   
14402 -1.572106e+20 -21084.307080  24.204781  77.290016  78.389455  76.729423   
14403 -1.014174e+20 -21190.114953  24.850367  77.290016  78.389455  76.729423   

       DynStdDev(1)  DynStd

In [15]:
display(masterdf['TIMESTAMP'].to_string())

'14500     2022-11-04 10:07:23.000000\n14501     2022-11-04 10:07:24.000000\n14502     2022-11-04 10:07:24.010000\n26701     2022-11-04 10:09:26.000000\n26702     2022-11-04 10:09:27.000000\n26703     2022-11-04 10:09:27.010000\n83910     2022-11-27 09:56:02.000000\n83911     2022-11-27 09:56:03.000000\n83912     2022-11-27 09:56:03.010000\n1134299   2022-11-27 15:09:03.000000\n1134300   2022-11-27 15:09:04.000000\n1134301   2022-11-27 15:09:04.010000\n39199     2022-11-27 16:06:32.000000\n39200     2022-11-27 16:06:33.000000\n39201     2022-11-27 16:06:33.010000\n1393899   2022-08-31 07:52:19.000000\n1393900   2022-08-31 07:52:19.000000\n1393901   2022-08-31 07:52:19.010000\n1394780   2022-08-31 07:52:27.800000\n1394781   2022-08-31 07:52:30.000000\n1394782   2022-08-31 07:52:30.010000\n1418199   2022-11-28 19:56:22.000000\n1418200   2022-11-28 19:56:23.000000\n1418201   2022-11-28 19:56:23.010000\n3703      2022-11-29 09:27:43.000000\n3704      2022-11-29 09:27:44.000000\n3705      2

In [ ]:
gpspklfiles = sorted(glob.glob(os.path.join(PKL_DIR,'*20hz*_gps.pkl')))
masterdf = pd.DataFrame()
for gpsfile in gpspklfiles:
    thisdf = pd.read_pickle(gpsfile)
    if len(masterdf.index)==0:
        masterdf = thisdf
    else:
        masterdf = pd.concat([masterdf, thisdf])
print(masterdf)

In [ ]:
MAXFILES=3
pklfiles = sorted(glob.glob(os.path.join(PKL_DIR,'*.pkl')))
lod=[]
for filenum, pklfile in enumerate(pklfiles[0:MAXFILES]):
    print(pklfile)
    df = pd.read_pickle(pklfile)
    #df=df.sort_values(by=['TIMESTAMP'])
    secs = np.array([x.timestamp() for x in df['TIMESTAMP']])
    secsdiff = secs[1:-1]-secs[0:-2]   
    for i in range(0,len(secsdiff)):
        thisdiff = secsdiff[i]
        if thisdiff > 0.012 or thisdiff < 0.008:
            print(thisdiff)
            mini = np.max(np.array([i-10,0]))
            maxi = np.min(np.array([i+10,len(secsdiff)]))
            print(df.iloc[mini:maxi])
    
    starttime=df.iloc[0]['TIMESTAMP']
    endtime=df.iloc[-1]['TIMESTAMP']
    timediff = (endtime - starttime)

    if timediff.seconds>4*60*60:
        #print('Problem likely with start time. Filter out all data more than 4 hours before end')
        df = df[df['TIMESTAMP']>endtime-pd.to_timedelta(4, unit='h')]
        df = df[df['TIMESTAMP']<=endtime]
        starttime=df.iloc[0]['TIMESTAMP']
        endtime=df.iloc[-1]['TIMESTAMP']
        timediff = (endtime - starttime)
    nrows=len(df.index)
    secs = np.array([x.timestamp() for x in df['TIMESTAMP']])
    secsdiff = secs[1:-1]-secs[0:-2]
    sample_interval = np.nanmedian(secsdiff)
    #sample_interval2 = timediff.seconds/(nrows-1)
    
    thisd = {}
    thisd['filename']=os.path.basename(pklfile)
    thisd['starttime']=starttime
    thisd['endtime']=endtime
    thisd['npts']=nrows
    thisd['nRECS']=df.iloc[-1]['RECORD']-df.iloc[0]['RECORD']+1
    thisd['Fs']=1/sample_interval
    lod.append(thisd)
lookuptableDF = pd.DataFrame(lod)
print(lookuptableDF)
lookuptableDF.to_csv('lookuptable.csv')

# 4. Check SDS data availability

In [ ]:
# Availability by day
startdate = obspy.UTCDateTime(2022,7,21)
enddate = obspy.UTCDateTime(2022,11,6)
sdsclient = open_sds(SDS_TOP)
trace_ids = sds_get_nonempty_traceids(sdsclient, startdate, enddate)
availabilityDF, trace_ids = sds_percent_available_per_day(sdsclient, startdate, enddate, speed=1, trace_ids=trace_ids)
del sdsclient

## to do
* add ability to plot availability. grayscale each day by percentage available

In [ ]:
import matplotlib.pyplot as plt
def get_yticks(s):
    yticklabels = []
    yticks=[]
    for i, el in enumerate(s.to_numpy()):
        yticklabels.append(el)
        yticks.append(i)
    ystep = 1
    if len(yticks)>15:
        ystep=2  
    if len(yticks)>25:
        ystep=3
    if len(yticks)>40:
        ystep=int(len(yticks)*7/100)        
    yticks = yticks[0::ystep]
    yticklabels = yticklabels[0::ystep]
    return (yticks, yticklabels)

def ontime_plot(data,xticklabels,yticks,yticklabels):
    # make ontime plot
    plt.rc('axes', labelsize=8) 
    fig = plt.figure(figsize=(5,5))
    ax = fig.add_subplot(111)
    #ax.imshow(data, aspect='auto', cmap=plt.cm.gray, interpolation='nearest')
    ax.imshow(np.transpose(data), aspect='auto', cmap=plt.cm.gray, interpolation='nearest')
    #plt.xticks(np.arange(len(xticklabels)), xticklabels)
    plt.yticks(np.arange(len(xticklabels)), xticklabels)
    #ax.set_xticklabels(xticklabels, rotation = 90)
    ax.set_yticklabels(xticklabels, rotation = 0, )
    #plt.yticks(yticks, yticklabels)
    plt.xticks(yticks, yticklabels, rotation = 90)
    bottom, top = ax.set_ylim()
    ax.set_ylim(bottom+1, top-1)
    #plt.tight_layout()
    return (fig, ax)


# Aren't these really independent NSLC's rather than just stations?

Adf = availabilityDF.iloc[:,1:]/100
Adata = np.array(Adf, dtype=float) # convert dataframe to numpy array
xticklabels = Adf.columns
print(xticklabels)
(yticks, yticklabels) = get_yticks(availabilityDF['date'])
print(yticks)
(fig, ax) = ontime_plot(1.0-Adata,xticklabels,yticks,yticklabels)
ax.tick_params(axis='both', which='major', labelsize=4)
#fig.tight_layout()
plt.xlabel('Date')
plt.ylabel('NSLC')
plt.rc('font', size=8) 
plt.rc('xtick', labelsize=8) 
plt.rc('ytick', labelsize=8) 
plt.grid('on')
plt.savefig('availability.pdf',dpi=300)


# 5. Read SDS archive and plot SDS archive for a rocket launch
Falcon 9 Block 5 | Starlink Group 4-35		September 24, 2022	SLC-40	23:32:10 UTC

In [ ]:
sdsclient = open_sds(SDS_TOP)
startt = obspy.UTCDateTime(2022,9,24,23,0,0)
endt = obspy.UTCDateTime(2022,9,24,23,59,59)
st = read_sds(sdsclient, startt, endt, trace_ids=trace_ids, speed=1)
print(st)
convert2units(st)
del sdsclient

st.plot(equal_scale=False);

In [ ]:
print(transducersDF)

In [ ]:
MAXFILES=3
pklfiles = sorted(glob.glob(os.path.join(PKL_DIR,'*.pkl')))
lod=[]
for filenum, pklfile in enumerate(pklfiles[0:MAXFILES]):
    print(pklfile)
    df = pd.read_pickle(pklfile)
    #df=df.sort_values(by=['TIMESTAMP'])
    secs = np.array([x.timestamp() for x in df['TIMESTAMP']])
    secsdiff = secs[1:-1]-secs[0:-2]   
    for i in range(0,len(secsdiff)):
        thisdiff = secsdiff[i]
        if thisdiff > 0.012 or thisdiff < 0.008:
            print(thisdiff)
            mini = np.max(np.array([i-10,0]))
            maxi = np.min(np.array([i+10,len(secsdiff)]))
            print(df.iloc[mini:maxi])
    
    starttime=df.iloc[0]['TIMESTAMP']
    endtime=df.iloc[-1]['TIMESTAMP']
    timediff = (endtime - starttime)

    if timediff.seconds>4*60*60:
        #print('Problem likely with start time. Filter out all data more than 4 hours before end')
        df = df[df['TIMESTAMP']>endtime-pd.to_timedelta(4, unit='h')]
        df = df[df['TIMESTAMP']<=endtime]
        starttime=df.iloc[0]['TIMESTAMP']
        endtime=df.iloc[-1]['TIMESTAMP']
        timediff = (endtime - starttime)
    nrows=len(df.index)
    secs = np.array([x.timestamp() for x in df['TIMESTAMP']])
    secsdiff = secs[1:-1]-secs[0:-2]
    sample_interval = np.nanmedian(secsdiff)
    #sample_interval2 = timediff.seconds/(nrows-1)
    
    thisd = {}
    thisd['filename']=os.path.basename(pklfile)
    thisd['starttime']=starttime
    thisd['endtime']=endtime
    thisd['npts']=nrows
    thisd['nRECS']=df.iloc[-1]['RECORD']-df.iloc[0]['RECORD']+1
    thisd['Fs']=1/sample_interval
    lod.append(thisd)
lookuptableDF = pd.DataFrame(lod)
print(lookuptableDF)
lookuptableDF.to_csv('lookuptable.csv')